In [1]:
import transformers
transformers.__version__

'4.10.0'

In [2]:
from transformers import T5Config, T5Model, load_tf_weights_in_t5

In [4]:
# !wget https://f000.backblazeb2.com/file/malaya-model/pretrained/t5-super-tiny-2021-07-28.tar.gz
# !tar -zxf t5-super-tiny-2021-07-28.tar.gz
# !rm t5-super-tiny-2021-07-28.tar.gz
!ls t5-super-tiny-v2

checkpoint                             model.ckpt-1000000.index
model.ckpt-1000000.data-00000-of-00002 model.ckpt-1000000.meta
model.ckpt-1000000.data-00001-of-00002 operative_config.gin


In [5]:
config = T5Config(
    vocab_size = 32128,
    n_positions=512,
    d_ff = 1024,
    d_kv = 64,
    d_model = 256,
    dropout_rate = 0.1,
    inputs_length = 512,
    num_heads = 6,
    num_layers = 2,
    decoder_start_token_id = 0,
    eos_token_id = 1,
    pad_token_id = 0)
print(config)
config.save_pretrained('./')

T5Config {
  "d_ff": 1024,
  "d_kv": 64,
  "d_model": 256,
  "decoder_start_token_id": 0,
  "dropout_rate": 0.1,
  "eos_token_id": 1,
  "feed_forward_proj": "relu",
  "gradient_checkpointing": false,
  "initializer_factor": 1.0,
  "inputs_length": 512,
  "is_encoder_decoder": true,
  "layer_norm_epsilon": 1e-06,
  "model_type": "t5",
  "n_positions": 512,
  "num_decoder_layers": 2,
  "num_heads": 6,
  "num_layers": 2,
  "pad_token_id": 0,
  "relative_attention_num_buckets": 32,
  "transformers_version": "4.10.0",
  "use_cache": true,
  "vocab_size": 32128
}



In [6]:
model = T5Model(config)
load_tf_weights_in_t5(model, config, 't5-super-tiny-v2/model.ckpt-1000000')

T5Model(
  (shared): Embedding(32128, 256)
  (encoder): T5Stack(
    (embed_tokens): Embedding(32128, 256)
    (block): ModuleList(
      (0): T5Block(
        (layer): ModuleList(
          (0): T5LayerSelfAttention(
            (SelfAttention): T5Attention(
              (q): Linear(in_features=256, out_features=384, bias=False)
              (k): Linear(in_features=256, out_features=384, bias=False)
              (v): Linear(in_features=256, out_features=384, bias=False)
              (o): Linear(in_features=384, out_features=256, bias=False)
              (relative_attention_bias): Embedding(32, 6)
            )
            (layer_norm): T5LayerNorm()
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (1): T5LayerFF(
            (DenseReluDense): T5DenseReluDense(
              (wi): Linear(in_features=256, out_features=1024, bias=False)
              (wo): Linear(in_features=1024, out_features=256, bias=False)
              (dropout): Dropout(p=0.1, inplace

In [7]:
from transformers import CONFIG_NAME, WEIGHTS_NAME
CONFIG_NAME, WEIGHTS_NAME

('config.json', 'pytorch_model.bin')

In [8]:
import torch

torch.save(model.state_dict(), './' + WEIGHTS_NAME)

In [9]:
from transformers import T5Config, T5Model, T5Tokenizer

In [10]:
# !wget https://f000.backblazeb2.com/file/malaya-model/bpe/sp10m.cased.ms-en.model

In [11]:
tokenizer = T5Tokenizer('sp10m.cased.ms-en.model')
tokenizer.save_pretrained('./')

('./tokenizer_config.json',
 './special_tokens_map.json',
 './spiece.model',
 './added_tokens.json')

In [12]:
tokenizer = T5Tokenizer.from_pretrained('./', lower = False)

In [13]:
config = T5Config.from_pretrained('./')

In [14]:
model = T5Model.from_pretrained('./pytorch_model.bin', config = config)

In [15]:
model.save_pretrained('./')

In [16]:
from transformers import T5Tokenizer, T5ForConditionalGeneration

In [17]:
model = T5ForConditionalGeneration.from_pretrained('./')

In [20]:
input_ids = tokenizer.encode('soalan: siapakah perdana menteri malaysia?', return_tensors = 'pt')
outputs = model.generate(input_ids)
tokenizer.decode(outputs[0])

'<pad> A.J. Morrow </i> <Tdikat</s>'

In [21]:
input_ids = tokenizer.encode('terjemah Inggeris ke Melayu: PETALING JAYA: Former prime minister Najib Razak has questioned whether the government knows how to manage the Covid-19 pandemic, outlining several seemingly contradictory announcements it has made.', return_tensors = 'pt')
outputs = model.generate(input_ids)
tokenizer.decode(outputs[0])

'<pad> PETALING JAYA: Bekas perdana menteri Najib Razak mempersoalkan sama ada kerajaan tahu bagaimana menguruskan pandemik'

In [22]:
input_ids = tokenizer.encode('terjemah Melayu ke Inggeris: PETALING JAYA: Pertemuan bekas Perdana Menteri, Datuk Seri Najib Tun Razak dan Timbalan Perdana Menteri, Datuk Seri Ismail Sabri Yaakob hari ini adalah bagi membincangkan isu berkaitan hala tuju dan dasar negara.', return_tensors = 'pt')
outputs = model.generate(input_ids)
tokenizer.decode(outputs[0])

'<pad> PETALING JAYA: The former Prime Minister, Datuk Seri Najib Tun Razak and Deputy Prime Minister,'

In [23]:
input_ids = tokenizer.encode('grafik pengetahuan: Keuskupan Agung Katolik Rom Maracaibo terletak di barat daya Keuskupan Katolik Rom Machiques.', return_tensors = 'pt')
outputs = model.generate(input_ids)
tokenizer.decode(outputs[0])

'<pad> Roman Catholic Archdiocese of Maracaibo shares border with Roman Catholic Diocese'

In [24]:
!rm -rf t5-super-tiny-v2